____________________
# Music 255: CRIM, XML, MEI, BeautifulSoup

In this Notebook, you can find an array of tools and techniques useful for navigating and analyzing MEI and XML files. 

* **Beautiful Soup's** documentation [here](https://www.crummy.com/software/BeautifulSoup/bs4/doc/)
* **XML** documentation can be found [here](https://www.w3schools.com/xml/xml_syntax.asp)
* **MEI** documentation and tools [here](https://music-encoding.org/).


### Find your pieces from the CRIM Corpus:

* Each of you will focus on ONE model and its derivative Mass.  Find your set [here](https://docs.google.com/spreadsheets/d/140JbgdPz1yBsbnF_umN3iq-nmC9drLgBtJ9Qd4hk6zE/edit#gid=0).

------
#### Setup: Importing Python Libraries

In [105]:
import os
from bs4 import BeautifulSoup as bs
import optparse
import sys
from pathlib import Path
import requests
import pandas as pd
from lxml import etree
import re
from collections import Counter
import glob
import verovio
from IPython.display import SVG, HTML
import matplotlib.pyplot as plt

----
### Section 1: Piece

In this part, we'll import a piece and investigate it starting with its **metadata**.

#### Step 1.1: Importing a file

If working **locally**, a good way to import a file is:

In [ ]:
# storing the local path
xml_doc = "CRIM_Model_0005.mei"

# opening and reading into a Soup object
with open(xml_doc) as file:
    soup_mei = bs(file, 'xml')

If working **remotely**, a good way to GET an MEI file at a URL is:

In [107]:
# function to extract xml document from given url
def getXML(url):
    # request for HTML document of given url
    response = requests.get(url)    
    # response will be provided in JSON format
    return response.text

# store URL
my_piece_url = "https://crimproject.org/mei/CRIM_Model_0001.mei"
# store response
remote_document = getXML(my_piece_url)
# convert to Soup
remote_soup_mei = bs(remote_document, 'xml')
soup_mei = remote_soup_mei

-----
### Step 2: Brief Look at the Data

In this section, we'll look at the raw version of the piece, its general contents, structure, authors, and other elements. We'll also search through tags and elements!

#### Step 2.1: Raw Data

We can print the XML contents of a file pretty easily:

In [108]:
print(soup_mei.prettify())

<?xml version="1.0" encoding="utf-8"?>
<?xml-model href="https://music-encoding.org/schema/4.0.1/mei-CMN.rng" type="application/xml" schematypens="http://relaxng.org/ns/structure/1.0"?>
<?xml-model href="https://music-encoding.org/schema/4.0.1/mei-CMN.rng" type="application/xml" schematypens="http://purl.oclc.org/dsdl/schematron"?>
<mei meiversion="4.0.0" xml:id="m-1" xmlns="http://www.music-encoding.org/ns/mei">
 <meiHead xml:id="m-2">
  <fileDesc xml:id="m-3">
   <titleStmt>
    <title>
     Veni speciosam
    </title>
    <respStmt>
     <persName auth="VIAF" auth.uri="http://viaf.org/viaf/42035469" role="composer">
      Johannes Lupi
     </persName>
     <persName role="editor">
      Marco Gurrieri
     </persName>
     <persName role="editor">
      Bonnie Blackburn
     </persName>
     <persName role="editor">
      Vincent Besson
     </persName>
     <persName role="editor">
      Richard Freedman
     </persName>
    </respStmt>
   </titleStmt>
   <pubStmt>
    <publisher>

#### Step 2.2: Overview

As you might have noticed, MEI documents consist of elements (marked by tags). Let's look at **all tags in this document**:

In [109]:
# find all the tags in the XML document, including the details of their contents
soup_mei.find_all(True)

[<mei meiversion="4.0.0" xml:id="m-1" xmlns="http://www.music-encoding.org/ns/mei">
 <meiHead xml:id="m-2">
 <fileDesc xml:id="m-3">
 <titleStmt>
 <title>
      Veni speciosam
     </title>
 <respStmt>
 <persName auth="VIAF" auth.uri="http://viaf.org/viaf/42035469" role="composer">
       Johannes Lupi
      </persName>
 <persName role="editor">
       Marco Gurrieri
      </persName>
 <persName role="editor">
       Bonnie Blackburn
      </persName>
 <persName role="editor">
       Vincent Besson
      </persName>
 <persName role="editor">
       Richard Freedman
      </persName>
 </respStmt>
 </titleStmt>
 <pubStmt>
 <publisher>
      Citations: The Renaissance Imitation Mass Project
     </publisher>
 <distributor>
      Centre d'Études Supérieures de la Renaissance
     </distributor>
 <distributor>
      Haverford CollegeMarco Gurrieri
     </distributor>
 <distributor>
      Bonnie Blackburn
     </distributor>
 <distributor>
      Vincent Besson
     </distributor>
 <distribut

In [110]:
# or the names of the tags (without contents)
for tag in soup_mei.find_all(True):
    print(tag.name)

mei
meiHead
fileDesc
titleStmt
title
respStmt
persName
persName
persName
persName
persName
pubStmt
publisher
distributor
distributor
distributor
distributor
distributor
date
availability
encodingDesc
appInfo
application
name
application
name
application
name
application
name
workList
work
title
composer
persName
classification
termList
term
manifestationList
manifestation
identifier
titleStmt
title
pubStmt
publisher
persName
date
physLoc
repository
corpName
settlement
identifier
music
body
mdiv
score
scoreDef
staffGrp
staffGrp
staffDef
label
instrDef
staffDef
label
instrDef
staffDef
label
instrDef
staffDef
label
instrDef
staffDef
label
instrDef
section
measure
tie
staff
layer
note
verse
syl
note
verse
syl
staff
layer
mRest
staff
layer
mRest
staff
layer
mRest
staff
layer
mRest
measure
staff
layer
note
note
verse
syl
note
verse
syl
note
verse
syl
staff
layer
rest
note
verse
syl
staff
layer
mRest
staff
layer
mRest
staff
layer
mRest
measure
staff
layer
note
note
note
note
staff
layer
note


We can **find specific tags**, too:

* Note that in an XML document you can specify some part of the tree on the way to the individual child tag, or go directly to those tags.  This could be useful if some element is reused at different places in your XML schema.

>`soup_mei.titleStmt.find_all("persName")`

or

>`soup_mei.find_all("persName")

In [111]:
soup_mei.titleStmt.find_all("persName")

[<persName auth="VIAF" auth.uri="http://viaf.org/viaf/42035469" role="composer">
       Johannes Lupi
      </persName>,
 <persName role="editor">
       Marco Gurrieri
      </persName>,
 <persName role="editor">
       Bonnie Blackburn
      </persName>,
 <persName role="editor">
       Vincent Besson
      </persName>,
 <persName role="editor">
       Richard Freedman
      </persName>]

And filter for those with a certain **attribute value**.

* Note that the values are specified as a dictionary:  `{'your_key': 'your_value'}` along with the tag name.

>`soup_mei.find_all("persName", {"role": "editor"})`

In [112]:
soup_mei.find_all("persName", {"role": "editor"})

[<persName role="editor">
       Marco Gurrieri
      </persName>,
 <persName role="editor">
       Bonnie Blackburn
      </persName>,
 <persName role="editor">
       Vincent Besson
      </persName>,
 <persName role="editor">
       Richard Freedman
      </persName>]

Sometimes, you might be working for scraping/analysis tools and would want to access the **contents (text)** of individual tags:

>`for tag in soup_mei.find_all("persName", {"role": "editor"}):
    print(tag.text.strip())`
    
The `.strip()` function assures that we remove whitespace and other useless code.

In [113]:
for tag in soup_mei.find_all("persName", {"role": "editor"}):
    print(tag.text.strip())

Marco Gurrieri
Bonnie Blackburn
Vincent Besson
Richard Freedman


Similarly, we can easily access the composer:

In [114]:
# the text of the composer element:
soup_mei.composer.text.strip()

'Johannes Lupi'

And the title:

In [115]:
# the text of the title element:
soup_mei.title.text.strip()

'Veni speciosam'

-----
### Step 3: Basics of Analysis

In this section, we'll start looking into how you would approach analyzing a CRIM piece.

#### Step 3.1: Staves, Measures, Notes

First, let's look at just one staff:

In [116]:
# just the first
soup_mei.staffDef

<staffDef clef.line="2" clef.shape="G" key.sig="1f" label="Superius" lines="5" n="1" xml:id="m-30">
<label>
          Superius
         </label>
<instrDef midi.channel="1" midi.pan="26" midi.volume="100" xml:id="m-32"/>
</staffDef>

Next, **find all staves**:

* Notice that these are returned as a **list** object, so we can easily also run this with a **for** loop.  

>`soup_mei.find_all("staffDef")`

* Beautiful Soup responses are "list ready".  Thus the first staff is `soup_mei.find_all("staffDef")[0]`.  The last staff is `soup_mei.find_all("staffDef")[-1]`.

In [117]:
# returns a list of ALL staves
soup_mei.find_all("staffDef")

[<staffDef clef.line="2" clef.shape="G" key.sig="1f" label="Superius" lines="5" n="1" xml:id="m-30">
 <label>
           Superius
          </label>
 <instrDef midi.channel="1" midi.pan="26" midi.volume="100" xml:id="m-32"/>
 </staffDef>,
 <staffDef clef.line="2" clef.shape="G" key.sig="1f" label="Contratenor" lines="5" n="2" xml:id="m-33">
 <label>
           Contratenor
          </label>
 <instrDef midi.channel="1" midi.pan="46" midi.volume="100" xml:id="m-35"/>
 </staffDef>,
 <staffDef clef.dis="8" clef.dis.place="below" clef.line="2" clef.shape="G" key.sig="1f" label="PrimusTenor" lines="5" n="3" xml:id="m-36">
 <label>
           PrimusTenor
          </label>
 <instrDef midi.channel="1" midi.pan="81" midi.volume="100" xml:id="m-38"/>
 </staffDef>,
 <staffDef clef.dis="8" clef.dis.place="below" clef.line="2" clef.shape="G" key.sig="1f" label="SecundusTenor" lines="5" n="4" xml:id="m-39">
 <label>
           SecundusTenor
          </label>
 <instrDef midi.channel="1" midi.pan="81

We can use the collection of Staves to figure out **what voices** are used in a piece:

In [118]:
for staff in soup_mei.find_all('staffDef'):
    print(staff.text.strip())

Superius
Contratenor
PrimusTenor
SecundusTenor
Bassus


Now, we can look for **specific staves** that satisfy our conditions:

In [119]:
# find ALL STAVES with a GIVEN CLEF by passing dictionary that specifies the requested type
# the final_all results are a bs list

# Get all Gs first
staves = soup_mei.find_all("staffDef", {'clef.shape': "G"})

# print cleaned-up text
for staff in staves:
    print(staff.text.strip())

Superius
Contratenor
PrimusTenor
SecundusTenor
Bassus


-----

### Step 3.2: Working with Children,  Siblings, and Parents

* First, let's find all **children** of the title Statement:


In [ ]:
# all the children of titleStmt.  What are they, and how long?
for item in soup_mei.titleStmt.children:
    print(item.name)

In [ ]:
# findChildren is a list, and so we can pick individual items
titleStmt = soup_mei.titleStmt.findChildren()
titleStmt[0]

In [ ]:
#recursive also gives a list
soup_mei.titleStmt.findChildren(recursive=True)

### Step 3.2b A report of siblings begins *after* the first instance of that tag.

Thus `soup_mei.titleStmt.persName` will find the first element of that type.  `soup_mei.titleStmt.persName.findNextSiblings()` will find all the siblings within that parent *after* the first element.

In [ ]:
# these are the NEXT sibs (after the first!)
names = soup_mei.titleStmt.persName.findNextSiblings()
names

### Step 3.2c Looking Parents allows us to go up the tree.

* Here we can find the tags going up from the bottom level of note:

>`for parent in soup_mei.note.find_parents():`
>>`print(parent.name)`

In [ ]:
for parent in soup_mei.note.find_parents():
    print(parent.name)

### Step 3.2c. You can add tags by looking up to the parent of a given tag.

>`people_involved_parent = soup_mei.find("persName").parent
new_person_tag = soup_mei.new_tag("persName", role="Analyst")
new_person_tag.string = "Oleh Shostak"
people_involved_parent.append(new_person_tag)
soup_mei.find_all("persName")`

In [ ]:
people_involved_parent = soup_mei.find("persName").parent
new_person_tag = soup_mei.new_tag("persName", role="Analyst")
new_person_tag.string = "Oleh Shostak"
people_involved_parent.append(new_person_tag)

soup_mei.find_all("persName")

### Step 4.  Counting Notes

We already know how to find the first note (of the first staff in the first bar):

>`soup_mei.note.get('pname')`

But we can also **find_all** notes, count and sort them by value:

>`len(soup_mei.find_all('note'))`

In [ ]:
# gets just the first pitch
soup_mei.note.get('pname')

In [ ]:
# how many notes?
len(soup_mei.find_all('note'))

In [ ]:
# gets just the first pitch
soup_mei.note.get('pname')

In [ ]:
# find all the notes and print pitch names
for note in soup_mei.find_all(name='note'):
    print(note.get('pname'))

Using some of the familiar techniques, we can count **pitches** and put them in a **series** or **DataFrame**:

In [ ]:
# counts pitches, now as dictionary
pitches = [n.get('pname') for n in soup_mei.find_all('note')]
counted = Counter(pitches)
counted_notes = pd.Series(counted).to_frame('count').sort_index()
counted_notes

And create a histogram

In [ ]:
counted_notes.plot(kind="bar", figsize=(15, 10))
plt.title("Pitch Distribution in My piece")
plt.xticks(rotation = 0)
plt.xlabel("Tone")
plt.ylabel("Count")
plt.show()


#### Working with Measures

It is oftentimes useful to look at **measures** – either all at once or specific ones. Here's an example:

In [ ]:
# last pitch in last measure, for each voice
measures = soup_mei.find_all('measure')
last_measure = measures[-1]
for staff in last_measure.find_all('staff'):
        note = staff.find_all('note')[-1]
        print(note.get('pname'))


Working with **Score Definitions** (scoreDef), it is possible to search for certain **events** within the piece. For example, find out where a **Time Signature change** occurs:

In [ ]:
scoredefs = soup_mei.find_all('scoreDef')
for scoredef in scoredefs:
    print(scoredef.get('meter.count'))
    print(scoredef.get('meter.unit'))
    next_measure = scoredef.find_next('measure', )
    print("The first bar with this TS is " + next_measure.get('n'))

Finally, we can look for some very specific things, like **all notes with a particular duration, pitch, and octave**:

* Use dictionary of key/value pairs to specify particular attributes.

>`soup_mei.find_all('note', {'dur': "4", 'pname': "g", 'oct': '3'})`

In [ ]:

soup_mei.find_all('note', {'dur': "4", 'pname': "g", 'oct': '3'})

### 4.0 Display your MEI with Verovio

* Verovio will render your piece directly in the Notebook.  It's the same library we use for CRIM.

In [ ]:


my_piece_url
response = requests.get(my_piece_url)
fetched_mei_string = response.text
# start the verovio toolkit and load the file there
tk = verovio.toolkit()
tk.loadData(fetched_mei_string)
tk.setScale(30)
tk.setOption( "pageHeight", "1500" )
tk.setOption( "pageWidth", "3000" )

tk.redoLayout()
# get the number of pages and display the music
count = tk.getPageCount()
for c in range(1, count + 1):
    music = tk.renderToSVG(c)
    display(SVG(music))

### 5.0 Save Revised XML document

>`f = open(title + '_' + 'rev_ts_longa' + '.xml', "w")`
    `f.write(str(soup))`
    `f.close()`

In [126]:
# regular expression to get CRIM Piece Id from URL:
title = re.findall("[^\\|/]+$", my_piece_url)
# Save with that CRIM ID as part of title
f = open(title + '_' + 'rev' + '.xml', "w")
    `f.write(str(soup))`
    `f.close()

['CRIM_Model_0001.mei']

In [ ]:
# BULK IMPORT LOCAL FILES

for name in glob.glob('local_folder'):
